In [2]:
from bs4 import BeautifulSoup
import requests
import re
import pymongo  
from pymongo import MongoClient
import pyodbc
from datetime import datetime
import sys
sys.path.append('../../') #:Used when importing MongoConnect
import time
import MongoConnect
import pandas as pd
import importlib
from selenium import webdriver
import os
import youtube_dl 


import pyace as pya
import gc
importlib.reload(pya)
headers = {
    'User-Agent':"Mozilla/5.0 (Windows NT 6.1; WOW64) AppleWebKit/537.1 (KHTML, like Gecko) Chrome/22.0.1207.1 Safari/537.1"
}  

song_train0410是待下載的歌曲 <br>
先整理出有幾首歌需要下載(需group_by(譜名+歌手名)來識別一首歌曲) <br>
然後先爬每首歌的Youtube URL並存在Mongo的Youtube_songtodownload_manyArttists資料表中

整理完後在 
# 每首歌曲的Youtube url爬蟲區塊爬URL


# 跳到Youtube Download 區塊是已經做完爬每首歌的youtube url後，把每個url撈出來下載歌曲並同時完成和弦辨識


In [5]:
song_train=pd.read_csv('../../../data/song_train0410.csv',encoding="ISO-8859-1")

In [6]:
song_train.head()

Unnamed: 0                       _id  artist  \
0           0  5cada0019fc5af34a460adaf  *NSync   
1           1  5cada0019fc5af34a460adb3  *NSync   
2           2  5cada0019fc5af34a460adb5  *NSync   
3           3  5cada0019fc5af34a460adb7  *NSync   
4           4  5cada0019fc5af34a460adc1  *NSync   

                                               chord  error rating  \
0  ['A', 'D', 'E', 'A', 'A', 'D', 'E', 'A', 'E', ...      0      6   
1  ['G#m', 'F#', 'E', 'F#', 'G#m', 'G#m', 'F#', '...      0    107   
2  ['Am', 'G', 'F', 'G', 'Am', 'Am', 'G', 'Dm', '...      0     16   
3  ['Am', 'G', 'F', 'F', 'G', 'Am', 'Am', 'Dm', '...      0      9   
4  ['G', 'C', 'D', 'Em7', 'G', 'C', 'D', 'G', 'G'...      0     63   

                                            tab_href  \
0  https://tabs.ultimate-guitar.com/tab/nsync/a_l...   
1  https://tabs.ultimate-guitar.com/tab/nsync/bye...   
2  https://tabs.ultimate-guitar.com/tab/nsync/bye...   
3  https://tabs.ultimate-guitar.com/tab/nsync/bye...   
4  https://tabs.ultimate-guitar.com/tab/nsync/god...   

                   tab_title version  
0  A Little More Time On You   Ver 1  
1                Bye Bye Bye   Ver 1  
2                Bye Bye Bye   Ver 2  
3                Bye Bye Bye   Ver 3  
4        God Must Have Spent   Ver 1

之後用'song_name' 欄位辨識是哪一歌曲

In [45]:
song_train['song_name']=song_train.tab_title+' '+song_train.artist
song_train.head()

Unnamed: 0                       _id  artist  \
0           0  5cada0019fc5af34a460adaf  *NSync   
1           1  5cada0019fc5af34a460adb3  *NSync   
2           2  5cada0019fc5af34a460adb5  *NSync   
3           3  5cada0019fc5af34a460adb7  *NSync   
4           4  5cada0019fc5af34a460adc1  *NSync   

                                               chord  error rating  \
0  ['A', 'D', 'E', 'A', 'A', 'D', 'E', 'A', 'E', ...      0      6   
1  ['G#m', 'F#', 'E', 'F#', 'G#m', 'G#m', 'F#', '...      0    107   
2  ['Am', 'G', 'F', 'G', 'Am', 'Am', 'G', 'Dm', '...      0     16   
3  ['Am', 'G', 'F', 'F', 'G', 'Am', 'Am', 'Dm', '...      0      9   
4  ['G', 'C', 'D', 'Em7', 'G', 'C', 'D', 'G', 'G'...      0     63   

                                            tab_href  \
0  https://tabs.ultimate-guitar.com/tab/nsync/a_l...   
1  https://tabs.ultimate-guitar.com/tab/nsync/bye...   
2  https://tabs.ultimate-guitar.com/tab/nsync/bye...   
3  https://tabs.ultimate-guitar.com/tab/nsync/bye...   
4  https://tabs.ultimate-guitar.com/tab/nsync/god...   

                   tab_title version                         song_name  
0  A Little More Time On You   Ver 1  A Little More Time On You *NSync  
1                Bye Bye Bye   Ver 1                Bye Bye Bye *NSync  
2                Bye Bye Bye   Ver 2                Bye Bye Bye *NSync  
3                Bye Bye Bye   Ver 3                Bye Bye Bye *NSync  
4        God Must Have Spent   Ver 1        God Must Have Spent *NSync

In [12]:
song_name_to_crawl=set(song_train.tab_title+' '+song_train.artist)

In [13]:
len(song_name_to_crawl),song_name_to_crawl

(11949,
 {'Last Tears Indigo Girls feat. Brandi Carlile',
  'Dress Up In You Belle and Sebastian',
  'My Last Date Skeeter Davis',
  'Its My Party Jessie J',
  'The Real World Owl City',
  'Firewood Regina Spektor',
  'Jesus Saves I Spend St. Vincent',
  'Lay Me Down Roll Me Out To Sea Glen Campbell',
  'Infatuation Maroon 5',
  'Contenders The Kinks',
  'Something Good Alt-J',
  'She Dont Like The Lights Justin Bieber',
  'Sex Yeah Marina and The Diamonds',
  'World On Fire Sarah McLachlan',
  'Glory And Gore Lorde',
  'Stop Whispering Radiohead',
  'One Night Elvis Presley',
  'This Is Saras Song Glen Campbell',
  'If I Ruled The World Glen Campbell',
  'Rap God Eminem',
  'Listening Wind Talking Heads',
  'What I Wanted To Say Colbie Caillat',
  'A Rush Of Blood To The Head Coldplay',
  'Adventure Of A Lifetime Coldplay',
  'Shiver Maroon 5',
  'Memo Years & Years',
  'Ive Gotta Get A Message Bee Gees',
  'Runnin Around Colbie Caillat',
  'Crown Of Love Arcade Fire',
  'Cold Case Lo

先從youtube網站搜尋關鍵字的第一個影片 <br>
如:搜尋A Day In The Life The Beatles <br>
然後抓第一個影片 <br>
然後要下載這個音檔 <br>
所以要先取得這個音檔的url


# 每首歌曲的Youtube url爬蟲

前面先整理出有幾首音檔要下載 <br>
把每首要下載的音檔的youtube影片url爬完 <br>
把url存在mongo <br>
之後再撈出來下載音檔並完成和弦辨識


In [14]:
driver = webdriver.Chrome()     # 打開Chrome 瀏覽器，webdriver.Chrome('下載的Chrome driver路徑.exe')


for song in song_name_to_crawl:
    
    url='https://www.youtube.com/results?search_query='+song

    try:
        driver.get(url)#請求網址
        page_html = driver.page_source
        soup1=BeautifulSoup(page_html,'lxml')
        song_yt_url=soup1.find('a',id='video-title')['href']
        song_yt_title=soup1.find('a',id='video-title')['title']
        bag={
            'song_yt_url':'https://www.youtube.com'+song_yt_url,
            'song_yt_title':song_yt_title,
            'song_name':song,
            'error':0
        }
    except Exception as e:
        bag={
            'song_name':song,
            'error':1
        }
    finally:
        db=MongoConnect.mongoconnect()
        one_document=db.Youtube_songtodownload_manyArttists
        one_document.insert_one(bag)
        print('insert success:',song)
        time.sleep(10)   

insert success: Last Tears Indigo Girls feat. Brandi Carlile
insert success: Dress Up In You Belle and Sebastian
insert success: My Last Date Skeeter Davis
insert success: Its My Party Jessie J
insert success: The Real World Owl City
insert success: Firewood Regina Spektor
insert success: Jesus Saves I Spend St. Vincent
insert success: Lay Me Down Roll Me Out To Sea Glen Campbell
insert success: Infatuation Maroon 5
insert success: Contenders The Kinks
insert success: Something Good Alt-J
insert success: She Dont Like The Lights Justin Bieber
insert success: Sex Yeah Marina and The Diamonds
insert success: World On Fire Sarah McLachlan
insert success: Glory And Gore Lorde
insert success: Stop Whispering Radiohead
insert success: One Night Elvis Presley
insert success: This Is Saras Song Glen Campbell
insert success: If I Ruled The World Glen Campbell
insert success: Rap God Eminem
insert success: Listening Wind Talking Heads
insert success: What I Wanted To Say Colbie Caillat
insert su

insert success: Close Your Eyes Westlife
insert success: Try Try Try Jason Mraz
insert success: Dont Stop Til You Get Enough Michael Jackson
insert success: Its Not Unusual Tom Jones
insert success: Let Me Be Your Teddy Bear Elvis Presley
insert success: Pinball Wizard Elton John
insert success: Youll Never Walk Alone Gerry & The Pacemakers
insert success: Stars-Rhinestone Cowboy Live Glen Campbell
insert success: Ill Be Edwin McCain
insert success: Utopia Lykke Li
insert success: Deja Vu Post MaloneFeat.Justin Bieber
insert success: Kogong Mark Forster
insert success: Breakfast In America Supertramp
insert success: Going Nowhere Little Mix
insert success: Help Me Make It Through The Night Glen Campbell
insert success: Take It Off Kesha
insert success: Mr Moonlight The Beatles
insert success: Alles Gute Silbermond
insert success: My Body Is A Cage Peter Gabriel
insert success: Today Glen Campbell
insert success: Never Let You Go Justin Bieber
insert success: A Million More Years Olly M

insert success: Nada Fue Un Error Julieta Venegas
insert success: Dick In A Box Justin Timberlake
insert success: Tar Baby Sade
insert success: Permanating Steven Wilson
insert success: Sunshower Glen Campbell
insert success: Menschenjunges Reinhard Mey
insert success: Nothing Would Be Better Nick Jonas
insert success: Silver Blue Roxette
insert success: Melting In The Sun Electric Light Orchestra
insert success: My Love Lionel Richie
insert success: Kansas City Hey Hey Hey The Beatles
insert success: Hercules Sara Bareilles
insert success: Outsider Marina and The Diamonds
insert success: Spooky Dusty Springfield
insert success: Salvation Gabrielle Aplin
insert success: Ruby Kenny Rogers
insert success: Evil Stevie Wonder
insert success: Turn Up The Music Chris Brown
insert success: Baby Dont Break My Heart Slow Taylor Swift
insert success: Often The Weeknd
insert success: Magic Coldplay
insert success: The Best Tina Turner
insert success: Please Me Cardi B feat. Bruno Mars
insert succ

insert success: Freestyle Lady Antebellum
insert success: Jackie Scott Walker
insert success: Memories Fade Tears for Fears
insert success: Wait For You Elliott Yamin
insert success: Promise To Try Madonna
insert success: I Was Made For Loving You Tori Kelly
insert success: So Far To Find You Casting Crowns
insert success: Dead In The Water Ellie Goulding
insert success: At Calvary Casting Crowns
insert success: Congratulations Blue October feat. Imogen Heap
insert success: Hello Goodbye The Beatles
insert success: Get Along Home Cindy Cindy Ricky Nelson
insert success: Forever Kenny Loggins
insert success: Timber Kesha
insert success: Outside The Weeknd
insert success: Mariners Apartment Complex Lana Del Rey
insert success: Put My Little Shoes Away Billie Joe Armstrong & Norah Jones
insert success: Change Lana Del Rey
insert success: Sukie In The Graveyard Belle and Sebastian
insert success: On A Goodnight Glen Campbell
insert success: I Will Be Christina Aguilera
insert success: As I

insert success: Hunter Dido
insert success: Wonderful Lady Gaga
insert success: Thank You Dido
insert success: Mirrors Justin Timberlake
insert success: Many The Miles Sara Bareilles
insert success: Cant See Straight Jamie Lawson with Ed Sheeran
insert success: Face In The Crowd Lionel Richie
insert success: Come To The Cross Michael W. Smith
insert success: I Cant Help Myself The Kelly Family
insert success: Uptown Girl Billy Joel
insert success: How To Love Justin Bieber
insert success: The Sharks And The Crows Woodkid
insert success: Elle Me Dit Mika
insert success: Young And Beautiful Elvis PresleyWithThe Jordanaires
insert success: Only In Your Heart America
insert success: The Time Has Come Again The Last Shadow Puppets
insert success: Glorious Day Casting Crowns
insert success: Whenever Wherever Shakira
insert success: Come And Buy My Toys David Bowie
insert success: Hope Is A Dangerous Thing For A Woman Like Me To Have - But I Have It Lana Del Rey
insert success: Need Her Love 

...

insert success: Cant Smile Without You Carpenters
insert success: I Cant Make It Alone Dusty Springfield
insert success: Smoke Clouds James Arthur
insert success: I Cant Hear The Music James Blunt
insert success: Standing Next To Me The Last Shadow Puppets
insert success: Winners Never Quit Owl City
insert success: High For This The Weeknd
insert success: The Circus Take That
insert success: Copilot Helene Fischer
insert success: Black And White Regina Spektor
insert success: Im Alright Taylor Swift
insert success: Back To The Start Lily Allen
insert success: One Of The Brightest Stars James Blunt
insert success: I Knew Jesus Before He Was A Superstar Glen Campbell
insert success: Bluebird Christina Perri
insert success: Haru Haru Big Bang
insert success: Hey Girl Lady Gaga feat. Florence Welch
insert success: Standing In Front Of You Kelly Clarkson
insert success: Mr Night Kenny Loggins
insert success: One Hundred Miles Away From Home Glen Campbell
insert success: I Could Be The One A

insert success: King Years & Years
insert success: Wooden Ships Crosby, Stills & Nash
insert success: Stuck In The Moment Justin Bieber
insert success: Cortez The Killer Indigo Girls
insert success: I Cant Decide Scissor Sisters
insert success: How Deep Is Your Love Take That
insert success: Chasing Cars Ed Sheeran
insert success: Thinking Of You Kesha
insert success: My Blood Ellie Goulding
insert success: Breaking It Up Lykke Li
insert success: Street Spirit Fade Out Radiohead
insert success: Memories Leonard Cohen
insert success: Optimistic Radiohead
insert success: Rolling In The Deep Adele
insert success: Out On My Own Gabrielle Aplin
insert success: Misery The Beatles
insert success: Mijn Vlakke Land Jacques Brel
insert success: Bluebird Sara Bareilles
insert success: Live To Party Jonas Brothers
insert success: Dreamer Supertramp
insert success: Love Letters Elvis Presley
insert success: She The Monkees
insert success: Being With You Smokey Robinson
insert success: They Cant Tak

insert success: Get On Your Knees Nicki Minaj feat. Ariana Grande
insert success: Please Come To Boston Glen Campbell
insert success: Tunnel Vision Justin Timberlake
insert success: Call It Even Glen Campbell
insert success: Move You Kelly Clarkson
insert success: Carry On Norah Jones
insert success: Your Love Is My Love Whitney Houston
insert success: Highwayman Glen Campbell
insert success: Whos To Say Vanessa Carlton
insert success: White Crosses Edwin McCain
insert success: Love Goes On Kelly Clarkson
insert success: I Am Here P!nk
insert success: Wearin That Loved On Look Elvis Presley
insert success: White Teeth Teens Lorde
insert success: Calvary Bon Iver
insert success: 15 Step Radiohead
insert success: Scary Monsters And Supercreeps David Bowie
insert success: Amazing Grace Elvis Presley
insert success: Vegas Lights Panic! At the Disco
insert success: Cleanin Out My Closet solo Eminem
insert success: Anothers Arms Coldplay
insert success: Papa Dont Preach Madonna
insert succes

insert success: Santa Tell Me Ariana Grande
insert success: Petals Mariah Carey
insert success: Just My Type The Vamps
insert success: Trap Queen Ed Sheeran
insert success: Stupid In Love Rihanna
insert success: Didnt I Rod Stewart
insert success: Quiet Demi Lovato
insert success: Empire Shakira
insert success: A Whiter Shade Of Pale Joe Cocker
insert success: Scarecrow Alex & Sierra
insert success: Gimmie Love Carly Rae Jepsen
insert success: Mudhouse Gypsy Mc Jason Mraz
insert success: In My Defence Freddie Mercury
insert success: Move To Town Milow
insert success: Here You Come Again Dolly Parton
insert success: First Of May Bee Gees
insert success: Le Moribond Jacques Brel
insert success: Like Spinning Plates  Live Radiohead
insert success: Lonely Wine Roy Orbison
insert success: Feels Like Home Bonnie Raitt
insert success: Small Bills Regina Spektor
insert success: Did Trouble Me Tom Jones
insert success: After Loving You Elvis Presley
insert success: Dream A Little Dream Of Me (v

insert success: A Star Is Born - Is That Alright Misc Soundtrack/Lady Gaga
insert success: One Moment In Time Whitney Houston
insert success: Eyelashes Tori Kelly
insert success: I Wanna Go Britney Spears
insert success: Brand New Day Sting
insert success: I Can Wait Forever Air Supply
insert success: The Fight Sia
insert success: Rain YUI
insert success: La Dame De Haute-Savoie Francis Cabrel
insert success: Louise Bonnie Raitt
insert success: Im Leavin Elvis Presley
insert success: This Song Is About You Olly Murs
insert success: Never Gonna Leave This Bed Maroon 5
insert success: Say Goodbye To Hollywood Billy Joel
insert success: Jesus Born On This Day Mariah Carey
insert success: Bad Influence P!nk
insert success: Donkey Jaw America
insert success: Mystic Knights The Kelly Family
insert success: My Love Westlife
insert success: Gimme Gimme Gimme ABBA
insert success: The Laughing Gnome David Bowie
insert success: Dont Say Its Too Late Westlife
insert success: Glory Road Neil Diamon

# Youtube Download 
用每個youtube影片的url下載音檔

In [3]:
#Youtube_has_downloaded_manyArtists:已經做完和弦辨識的歌曲
db=MongoConnect.mongoconnect()
one_document=db.Youtube_has_downloaded_manyArtists
list=one_document.find({})
has_downloaded_list=[]
load=0
for i in list:
    load=load+1
    if(load % 100==0):print(load)
    has_downloaded_list.append(i['song_yt_url'])

100
200
300
400
500


In [6]:
print(len(has_downloaded_list),'筆歌曲完成和弦辨識')

598 筆歌曲完成和弦辨識


In [7]:
db=MongoConnect.mongoconnect()
one_document=db.Youtube_songtodownload_manyArttists
list=one_document.find({ 'song_yt_url': { '$nin': has_downloaded_list } } )
download_list=[]
load=0
for i in list:
    load=load+1
    if(load % 100==0):print(load)
    download_list.append(i)


100
200
300
400
500
600
700
800
900
1000
1100
1200
1300
1400
1500
1600
1700
1800
1900
2000
2100
2200
2300
2400
2500
2600
2700
2800
2900
3000
3100
3200
3300
3400
3500
3600
3700
3800
3900
4000
4100
4200
4300
4400
4500
4600
4700
4800
4900
5000
5100
5200
5300
5400
5500
5600
5700
5800
5900
6000
6100
6200
6300
6400
6500
6600
6700
6800
6900
7000
7100
7200
7300
7400
7500
7600
7700
7800
7900
8000
8100
8200
8300
8400
8500
8600
8700
8800
8900
9000
9100
9200
9300
9400
9500
9600
9700
9800
9900
10000
10100
10200
10300
10400
10500
10600
10700
10800
10900
11000
11100
11200


In [8]:
print(len(download_list),'筆歌曲未完成和弦辨識')

11280 筆歌曲未完成和弦辨識


In [9]:
sum(pd.DataFrame(download_list)['song_yt_url'].isin(has_downloaded_list))

0

In [10]:
pd.DataFrame(download_list).head()

_id  error                      song_name  \
0  5caf0ab29fc5af060c7c6d8c      0          La Bikina Luis Miguel   
1  5caf0abd9fc5af060c7c6d8e      0  Back To Manhatten Norah Jones   
2  5caf0ac89fc5af060c7c6d90      0        Aquarius Regina Spektor   
3  5caf0ad39fc5af060c7c6d92      0      Beach Shack Elvis Presley   
4  5caf0ade9fc5af060c7c6d94      0         Corrida Francis Cabrel   

                               song_yt_title  \
0  Luis Miguel - "La Bikina" (Video Oficial)   
1            Norah Jones - Back To Manhattan   
2                    Aquarius Regina Spektor   
3               Elvis sings Beach Shack (HD)   
4                La Corrida - Francis Cabrel   

                                   song_yt_url  
0  https://www.youtube.com/watch?v=NCvJwzDQTBM  
1  https://www.youtube.com/watch?v=FX4Dq1mgCRk  
2  https://www.youtube.com/watch?v=eGx1qekdCjE  
3  https://www.youtube.com/watch?v=KLhrbqLBq4w  
4  https://www.youtube.com/watch?v=m1ET6SEtwbc

In [11]:
for i in download_list:
    print(i['song_yt_url'])

https://www.youtube.com/watch?v=NCvJwzDQTBM
https://www.youtube.com/watch?v=FX4Dq1mgCRk
https://www.youtube.com/watch?v=eGx1qekdCjE
https://www.youtube.com/watch?v=KLhrbqLBq4w
https://www.youtube.com/watch?v=m1ET6SEtwbc
https://www.youtube.com/watch?v=NTzYYmQxwnk
https://www.youtube.com/watch?v=2qdhJxvS6eE
https://www.youtube.com/watch?v=ruJnPqdxmTs
https://www.youtube.com/watch?v=_K0UKms267c
https://www.youtube.com/watch?v=jpJ8CbrWX_Y
https://www.youtube.com/watch?v=eA9Xltmmfb4
https://www.youtube.com/watch?v=BKMuwfC4lDE
https://www.youtube.com/watch?v=ppfVAOzKJxs
https://www.youtube.com/watch?v=4LdUme7QZLY
https://www.youtube.com/watch?v=kle2xHhRHg4
https://www.youtube.com/watch?v=zGEvB6UOcKs
https://www.youtube.com/watch?v=p5rQHoaQpTw
https://www.youtube.com/watch?v=TZFQgqhNoEI
https://www.youtube.com/watch?v=jRFMZpLWzCM
https://www.youtube.com/watch?v=_ut11U4JupI
https://www.youtube.com/watch?v=5ifN8aIkE1U
https://www.youtube.com/watch?v=qYVpo6LHao4
https://www.youtube.com/watch?v=

https://www.youtube.com/watch?v=pG8qkjI5bJQ
https://www.youtube.com/watch?v=FfXLL57T0ls
https://www.youtube.com/watch?v=Q_ljNRC8qqM
https://www.youtube.com/watch?v=FfQfgFmS7rg
https://www.youtube.com/watch?v=Bc3sml-EOs4
https://www.youtube.com/watch?v=AMI6dFNteZM
https://www.youtube.com/watch?v=g0WluiqFwec
https://www.youtube.com/watch?v=6xxqVI57LpU
https://www.youtube.com/watch?v=n7t8IaeWxCA
https://www.youtube.com/watch?v=imi9Smkt_cI
https://www.youtube.com/watch?v=rshm6hWkxVA
https://www.youtube.com/watch?v=2fngvQS_PmQ
https://www.youtube.com/watch?v=2VH6slAuq2o
https://www.youtube.com/watch?v=OKMSgZo9c8s
https://www.youtube.com/watch?v=Cy2BgVcCLJA
https://www.youtube.com/watch?v=tuunqfdz388
https://www.youtube.com/watch?v=x6MDhtBEmCs
https://www.youtube.com/watch?v=VUzlQjBwfoE
https://www.youtube.com/watch?v=dNm0b2SCXxY
https://www.youtube.com/watch?v=ZYqgGbCEmOw
https://www.youtube.com/watch?v=OiPiRKbNCWY
https://www.youtube.com/watch?v=v_I-z_AJ_4Q
https://www.youtube.com/watch?v=

KeyError: 'song_yt_url'

In [27]:
#下載範例
#download_song('https://www.youtube.com/watch?v=u3cKrp96i_M','海上的人')


In [12]:
def download_song(song_url, song_title):
    """
    Download a song using youtube url and song title
    """

    outtmpl = song_title + '.%(ext)s'
    ydl_opts = {
        'format': 'bestaudio/best',
        'outtmpl': outtmpl,
        'postprocessors': [{
            'key': 'FFmpegExtractAudio',
            'preferredcodec': 'mp3',
            'preferredquality': '192',
        }],

    }

    with youtube_dl.YoutubeDL(ydl_opts) as ydl:
        info_dict = ydl.extract_info(song_url, download=True) 

In [ ]:
#執行下載
download_dir='C:/Users/dcw10/Python jupyter code/Ultimate_GuitarTab_Craw/ultimate-guitar-tab-crawl/Python_code/youtube_song_download/'
os.chdir(download_dir)

download_list_row=0
#下載歌曲時也作和弦辨識得到該曲的和弦
for i  in download_list:
    try:
        download_list_row +=1
        link = i['song_yt_url']
        song_name=i['song_name']
        
        #下載歌曲:
        download_song(link,song_name) 
        
        #辨識下載的歌曲的和弦:
        songpath='./'+song_name+'.mp3'
        respath='.chords.txt'
        modelpath='C:\\Users\\dcw10\\Python jupyter code\\pyace-master\\pretrained_model\\model\\lstmrnn512\\CJKURB.cg.model'
        acemode='rnn'
        
        chord_infor=pya.deepace(songpath,respath,acemode,modelpath)
       
        bag={
            'song_yt_url':link,
            'song_name':song_name,
            'song_detector_chord':chord_infor,
            'error':0
        }
       
            
        
    except Exception as e:
        print(e)
        print('這首歌無法下載或作和弦辨識時有問題')
       
        bag={
            'song_yt_url':link,
            'song_name':song_name,
            'song_detector_chord':'',
            'error':1
        }
    finally:
        print('目前進行到第',download_list_row,'筆')
        db=MongoConnect.mongoconnect()
        one_document=db.Youtube_has_downloaded_manyArtists
        one_document.insert_one(bag)
        print('insert success:',song_name)
        time.sleep(10) 
        
        gc.collect()

[youtube] NCvJwzDQTBM: Downloading webpage
[youtube] NCvJwzDQTBM: Downloading video info webpage
[download] La Bikina Luis Miguel.webm has already been downloaded
[download] 100% of 2.93MiB
[ffmpeg] Destination: La Bikina Luis Miguel.mp3
Deleting original file La Bikina Luis Miguel.webm (pass -k to keep)
feature extraction...
hmm setup...
generating segmentation...
segment tiling...
classifying...


C:\ProgramData\Anaconda3\lib\site-packages\numpy\core\fromnumeric.py:2920: RuntimeWarning: Mean of empty slice.
  out=out, **kwargs)
C:\ProgramData\Anaconda3\lib\site-packages\numpy\core\_methods.py:78: RuntimeWarning: invalid value encountered in true_divide
  ret, rcount, out=ret, casting='unsafe', subok=False)


generating output...
retrieve chord_info successfully
目前進行到第 1 筆
insert success: La Bikina Luis Miguel
[youtube] FX4Dq1mgCRk: Downloading webpage
[youtube] FX4Dq1mgCRk: Downloading video info webpage
[download] Destination: Back To Manhatten Norah Jones.webm
[download] 100% of 4.21MiB in 00:01                          
[ffmpeg] Destination: Back To Manhatten Norah Jones.mp3
Deleting original file Back To Manhatten Norah Jones.webm (pass -k to keep)
feature extraction...
hmm setup...
generating segmentation...
segment tiling...
classifying...
generating output...
retrieve chord_info successfully
目前進行到第 2 筆
insert success: Back To Manhatten Norah Jones
[youtube] eGx1qekdCjE: Downloading webpage
[youtube] eGx1qekdCjE: Downloading video info webpage
[download] Destination: Aquarius Regina Spektor.webm
[download] 100% of 5.26MiB in 00:01                  
[ffmpeg] Destination: Aquarius Regina Spektor.mp3
Deleting original file Aquarius Regina Spektor.webm (pass -k to keep)
feature extractio

feature extraction...
hmm setup...
generating segmentation...
segment tiling...
classifying...
generating output...
retrieve chord_info successfully
目前進行到第 16 筆
insert success: Everything Youre Not Demi Lovato
[youtube] p5rQHoaQpTw: Downloading webpage
[youtube] p5rQHoaQpTw: Downloading video info webpage
[download] Destination: Bennie And The Jets Elton John.webm
[download] 100% of 4.61MiB in 00:00                  
[ffmpeg] Destination: Bennie And The Jets Elton John.mp3
Deleting original file Bennie And The Jets Elton John.webm (pass -k to keep)
feature extraction...
hmm setup...
generating segmentation...
segment tiling...
classifying...
generating output...
retrieve chord_info successfully
目前進行到第 17 筆
insert success: Bennie And The Jets Elton John
[youtube] TZFQgqhNoEI: Downloading webpage
[youtube] TZFQgqhNoEI: Downloading video info webpage
[download] Destination: Somethings Got A Hold On Me Christina Aguilera.webm
[download] 100% of 3.09MiB in 00:00                          
[f

[download] 100% of 4.76MiB in 00:00                          
[ffmpeg] Destination: I Aint Gonna Stand For It Stevie Wonder.mp3
Deleting original file I Aint Gonna Stand For It Stevie Wonder.webm (pass -k to keep)
feature extraction...
hmm setup...
generating segmentation...
segment tiling...
classifying...
generating output...
retrieve chord_info successfully
目前進行到第 31 筆
insert success: I Aint Gonna Stand For It Stevie Wonder
[youtube] 0_LxYmL89Tw: Downloading webpage
[youtube] 0_LxYmL89Tw: Downloading video info webpage
[download] Destination: Es Gibt Tage Da Wnscht Ich Ich Wr Mein Hund Reinhard Mey.webm
[download] 100% of 2.24MiB in 00:01                  
[ffmpeg] Destination: Es Gibt Tage Da Wnscht Ich Ich Wr Mein Hund Reinhard Mey.mp3
Deleting original file Es Gibt Tage Da Wnscht Ich Ich Wr Mein Hund Reinhard Mey.webm (pass -k to keep)
feature extraction...
hmm setup...
generating segmentation...
segment tiling...
classifying...
generating output...
retrieve chord_info successful

...

[download] 100% of 2.50MiB in 00:00                  
[ffmpeg] Correcting container in "Youve Got To Hide Your Love Away (ver#11) The Beatles.m4a"
[ffmpeg] Destination: Youve Got To Hide Your Love Away (ver#11) The Beatles.mp3
Deleting original file Youve Got To Hide Your Love Away (ver#11) The Beatles.m4a (pass -k to keep)
feature extraction...
[Errno 22] Invalid argument: 'C:\\Users\\dcw10\\Python jupyter code\\Ultimate_GuitarTab_Craw\\ultimate-guitar-tab-crawl\\Python_code\\youtube_song_download\\Youve Got To Hide Your Love Away (ver?11) The Beatles.mp3'
這首歌無法下載或作和弦辨識時有問題
目前進行到第 9907 筆
insert success: Youve Got To Hide Your Love Away (ver?11) The Beatles
[youtube] qak0Zw6zPdo: Downloading webpage
[youtube] qak0Zw6zPdo: Downloading video info webpage
[download] Destination: Give Me Love Christina Perri.webm
[download] 100% of 3.84MiB in 00:00                  
[ffmpeg] Destination: Give Me Love Christina Perri.mp3
Deleting original file Give Me Love Christina Perri.webm (pass -k to k

generating output...
retrieve chord_info successfully
目前進行到第 9921 筆
insert success: Look Me In The Eyes Jonas Brothers
[youtube] -2W3_toVyO4: Downloading webpage
[youtube] -2W3_toVyO4: Downloading video info webpage
[download] Destination: Kissin In The Back Row Of The Movies The Drifters.webm
[download] 100% of 3.22MiB in 00:00                  
[ffmpeg] Destination: Kissin In The Back Row Of The Movies The Drifters.mp3
Deleting original file Kissin In The Back Row Of The Movies The Drifters.webm (pass -k to keep)
feature extraction...
hmm setup...
generating segmentation...
segment tiling...
classifying...
generating output...
retrieve chord_info successfully
目前進行到第 9922 筆
insert success: Kissin In The Back Row Of The Movies The Drifters
[youtube] GNhS7z36_7Q: Downloading webpage
[youtube] GNhS7z36_7Q: Downloading video info webpage
[download] Destination: The Gypsy Wife Leonard Cohen.webm
[download] 100% of 5.03MiB in 00:00                   
[ffmpeg] Destination: The Gypsy Wife Leo

ERROR: unable to download video data: HTTP Error 403: Forbidden


ERROR: unable to download video data: HTTP Error 403: Forbidden
這首歌無法下載或作和弦辨識時有問題
目前進行到第 9931 筆
insert success: Messiah Madonna
[youtube] 90iz99vk4jg: Downloading webpage
[youtube] 90iz99vk4jg: Downloading video info webpage
[download] Destination: Lloro Por Ti Enrique Iglesias.webm
[download] 100% of 3.97MiB in 00:00                   
[ffmpeg] Destination: Lloro Por Ti Enrique Iglesias.mp3
Deleting original file Lloro Por Ti Enrique Iglesias.webm (pass -k to keep)
feature extraction...
hmm setup...
generating segmentation...
segment tiling...
classifying...
generating output...
retrieve chord_info successfully
目前進行到第 9932 筆
insert success: Lloro Por Ti Enrique Iglesias
[youtube] 1EpljcxJmq4: Downloading webpage
[youtube] 1EpljcxJmq4: Downloading video info webpage
[download] Destination: Loyal Paloma Faith.webm
[download] 100% of 3.37MiB in 00:00                  
[ffmpeg] Destination: Loyal Paloma Faith.mp3
Deleting original file Loyal Paloma Faith.webm (pass -k to keep)
feature ext

Deleting original file Tonight Jonas Brothers.webm (pass -k to keep)
feature extraction...
hmm setup...
generating segmentation...
segment tiling...
classifying...
generating output...
retrieve chord_info successfully
目前進行到第 9946 筆
insert success: Tonight Jonas Brothers
[youtube] ScxZwXH09Ws: Downloading webpage
[youtube] ScxZwXH09Ws: Downloading video info webpage
[download] Destination: Moderation Florence + The Machine.webm
[download] 100% of 2.87MiB in 00:00                  
[ffmpeg] Destination: Moderation Florence + The Machine.mp3
Deleting original file Moderation Florence + The Machine.webm (pass -k to keep)
feature extraction...
hmm setup...
generating segmentation...
segment tiling...
classifying...
generating output...
retrieve chord_info successfully
目前進行到第 9947 筆
insert success: Moderation Florence + The Machine
[youtube] azas-1zInJ8: Downloading webpage
[youtube] azas-1zInJ8: Downloading video info webpage
[download] Destination: Secret World Peter Gabriel.webm
[download